In [1]:
pip install pandas

Defaulting to user installation because normal site-packages is not writeableNote: you may need to restart the kernel to use updated packages.




[notice] A new release of pip is available: 24.0 -> 24.1.2
[notice] To update, run: C:\Users\Alba GQ\AppData\Local\Microsoft\WindowsApps\PythonSoftwareFoundation.Python.3.12_qbz5n2kfra8p0\python.exe -m pip install --upgrade pip


In [2]:
import pandas as pd

file_path = "export_data_lodgings.csv"

data = pd.read_csv(file_path, sep=';')

print(data['Alojamientos'].head())


0    {"Casas rurales" : ["Habitación compartida en ...
1    {"Casas rurales" : ["Habitación en Gran Londre...
2    {"Casas rurales" : ["Bed and breakfast en Quin...
3    {"Casas rurales" : ["Casa de invitados en Maja...
4    {"Casas rurales" : ["Habitación en Schulzendor...
Name: Alojamientos, dtype: object


In [3]:
print("Columnas del DataFrame:")
print(data.columns)

Columnas del DataFrame:
Index(['Ciudad', 'Categorías', 'Alojamientos'], dtype='object')


In [4]:
print(data.to_string())

         Ciudad                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                          Categorías                                                                                                                                                                                                                                                                     

In [5]:
import json

data['Categorías'] = data['Categorías'].apply(json.loads)
data['Alojamientos'] = data['Alojamientos'].apply(json.loads)


In [6]:
possible_categories = [
    'Casas rurales', 'A pie de playa', 'Cabañas', 'Minicasas', 'Castillos', 'Singulares', 'Granjas', 'Lagos', 'Camping',
    'Parques nacionales', 'Mansiones', 'Barcos', 'Casas del árbol', 'Casas domo', 'Remotos', 'Viñedos', 'Habitaciones',
    'Para jugar', 'Luxe', 'Casas flotantes', 'Surf', 'Esquí', 'Cabañas triangulares', 'Tropical', 'Graneros', 'Golf',
    'Casas particulares', 'Riads', 'En las alturas', 'Adaptados', 'Desiertos', 'Molinos', 'Caravanas', 'Playas'
]

# Dividir la lista en tres columnas
num_columns = 3
num_rows = (len(possible_categories) + num_columns - 1) // num_columns
columns = [possible_categories[i * num_rows: (i + 1) * num_rows] for i in range(num_columns)]

# Formatear el texto en tres columnas
category_list_text = ''
for i in range(num_rows):
    col_texts = []
    for j in range(num_columns):
        index = i + j * num_rows + 1
        if i < len(columns[j]):
            col_texts.append(f"{index} - {columns[j][i]}")
        else:
            col_texts.append('')

    category_list_text += f"{col_texts[0]:<35} {col_texts[1]:<35} {col_texts[2]}\n"


In [7]:
explanation_text = '''
Vamos a buscarte en que ciudades están las posibles combinaciones de las categorías que elijas.
A continuación te daremos un listado de todas las categorías posibles, y podrás seleccionar 1 o varias poniendo el número de las categorías que quieras. 
En caso de que quieras varias separalas con una `,`.
'''

#docstrings declarado dentro d ela funcion para que no afecte de manera global
def ask_categories():
    print(explanation_text)
    print(category_list_text)
    input_answer = input("¿Por qué categorías quieres filtrar?")

    categories_number_selected_raw = input_answer.split(",")
    categories_number_selected_clean =  [i.strip('[]') for i in categories_number_selected_raw]
    categories_selected = []
    for category_number in categories_number_selected_clean:
        try:
            categories_selected.append(possible_categories[int(category_number)-1])
        except Exception as e:
            print(f"Category {category_number} not found")

    print(f"Has seleccionado: {', '.join(categories_selected)}\n") # For development

    result = data[data['Categorías'].apply(lambda x: all(x.get(cat, False) for cat in categories_selected))]["Ciudad"]
    result_list = result.tolist()

    if(len(result_list) > 0):
        ciudades = ', '.join(result.tolist())
        print("Las ciudades a las que puedes ir son:", ciudades)



        # Pregunta al usuario si está conforme con los resultados
        conforme = input("¿Estás conforme con estos resultados? (sí/no): ").strip().lower()
        if conforme in ['sí', 'si', 'yes']:
            ciudad_seleccionada = input("Selecciona una ciudad de la lista anterior: ").strip()
            if ciudad_seleccionada in result_list:
                # Muestra los alojamientos para la ciudad seleccionada
                ciudad_data = data[data['Ciudad'] == ciudad_seleccionada].iloc[0]
                alojamientos = ciudad_data['Alojamientos']
                print(f"\nAlojamientos en {ciudad_seleccionada} para las categorías seleccionadas:")
                for categoria in categories_selected:
                    print(f"- {categoria}: {', '.join(alojamientos.get(categoria, []))}")
            else:
                print("La ciudad seleccionada no está en la lista.")
        elif conforme in ['no', 'no']:
            print("Volvamos a intentar con otros filtros.")
        else:
            print("Respuesta no válida. Volvamos a intentar con otros filtros.")
    else:
        print("No hay ciudades disponibles para esa selección. Por favor intenta de nuevo.")

ask_categories()


Vamos a buscarte en que ciudades están las posibles combinaciones de las categorías que elijas.
A continuación te daremos un listado de todas las categorías posibles, y podrás seleccionar 1 o varias poniendo el número de las categorías que quieras. 
En caso de que quieras varias separalas con una `,`.

1 - Casas rurales                   13 - Casas del árbol                25 - Graneros
2 - A pie de playa                  14 - Casas domo                     26 - Golf
3 - Cabañas                         15 - Remotos                        27 - Casas particulares
4 - Minicasas                       16 - Viñedos                        28 - Riads
5 - Castillos                       17 - Habitaciones                   29 - En las alturas
6 - Singulares                      18 - Para jugar                     30 - Adaptados
7 - Granjas                         19 - Luxe                           31 - Desiertos
8 - Lagos                           20 - Casas flotantes                32 - Molin